## Loading data

The upcoming section consists of a few preparatory steps such as: (I.) preparing environment and loading packages necessary for the further steps, (II.) loading sequencing data, (III.) removing outlier and random samples to equalize a number of replicates per group and (IV.) normalizing data using a rarefaction.   

In [66]:
import sys
import copy

sys.path.append("/home/adam/miseq/seqDataClass")

import pandas as pd
import numpy as np
import random

#import seqDataClass.seqDataClass as seqDataClass
import seqDataClass as seqDataClass

data = seqDataClass.seqObject(mappingFile="/home/adam/miseq/ReverseTrans/mapping.csv", 
                              taxonomyFile= "/home/adam/miseq/ReverseTrans/taxonomy.csv", 
                              otuFile="/home/adam/miseq/ReverseTrans/otutab.txt", 
                              taxonomySep=',',
                              sampleNamesColumn="Name")

#print(data.data.sum(axis=0))

# Removing outlier samples
bad_samples = ["Osnat056", "Osnat045", "Osnat055"]

for sample in bad_samples:
    print("Removing bad sample : {}".format(sample))
    data.remove_sample(category="Name", sample=sample)
    
# Randomply removing samples from the data set
TGIRT = ["Osnat037", "Osnat038", "Osnat039", "Osnat040", "Osnat041", "Osnat042", "Osnat043"]

tgirtChoice = random.sample(TGIRT, 1)

for sample in tgirtChoice:
    print("Removing randomly: {} from TGIRT".format(sample))
    data.remove_sample(category="Name", sample=sample)

promega55 = ["Osnat059", "Osnat060", "Osnat061", "Osnat062"]
promega55Choice = random.sample(promega55, 2)   # Randomly select an element from a list

for sample in promega55Choice:
    print("Removing randomly: {} from ImPromII 55°C".format(sample))
    data.remove_sample(category="Name", sample=sample)

data.rarefy_to_even_depth(seqDepth=10000,seed=124)

#print(data.data.sum(axis=0))

data.add_otu_parameter(yamlParamDictFile="/home/adam/miseq/ReverseTrans/GC_content_plot/otus_GC.yaml", paramName="GC_content")

Removing bad sample : Osnat056
Removing bad sample : Osnat045
Removing bad sample : Osnat055
Removing randomly: Osnat039 from TGIRT
Removing randomly: Osnat060 from ImPromII 55°C
Removing randomly: Osnat061 from ImPromII 55°C
Sample Osnat038 was removed from the dataset because it contains insufficient amount of sequences (34).
Sample Osnat048 was removed from the dataset because it contains insufficient amount of sequences (121).


In [2]:
data.save_otu_csv(fileName="/home/adam/miseq/ReverseTrans/normalized_tab.csv")

## Saving data for downstream analysis

Data is normalized by column the results are presented in a table. Following that, only an upper quartile of the classes is further normalized by row (class) and the result is used for the GC relative enrichment plot. 

In [67]:
# A copy of the original data frame
df1 = data.data.copy()

# Making a sum on the class and enzyme level
#df1 = df1.sum(level="Class", axis=0)
df1 = df1.sum(level="Enzyme", axis=1)

# Calculating a sum per enzyme category to normalize 
colSum = df1.groupby("Class").sum()

df2 = df1.div(colSum)

The data frame is simplified to only a class level information, OTU names, GC content and the four enzymatic conditions. 

In [68]:
df2 = df2.copy()
df2 = df2.reset_index()
df3 = df2.drop(["Domain","Phylum", "Order", "Family", "Genus"], axis=1)
df3

Enzyme                Class      OTU  GC_content     TGIRT  SuperScriptIV  \
0          Oxyphotobacteria  Otu0001    0.547847  0.831243       0.855056   
1            Actinobacteria  Otu0002    0.572127  0.155554       0.204453   
2       Alphaproteobacteria  Otu0003    0.579208  0.144691       0.110718   
3       Gammaproteobacteria  Otu0004    0.550117  0.040373       0.033656   
4       Alphaproteobacteria  Otu0005    0.559406  0.130238       0.125370   
5       Alphaproteobacteria  Otu0006    0.522277  0.053371       0.046098   
6       Alphaproteobacteria  Otu0007    0.564356  0.030198       0.039430   
7       Alphaproteobacteria  Otu0008    0.559406  0.042471       0.050379   
8       Alphaproteobacteria  Otu0009    0.574257  0.027937       0.028153   
9       Deltaproteobacteria  Otu0010    0.567757  0.211929       0.163642   
10            Rubrobacteria  Otu0011    0.602804  0.286221       0.329832   
11           Actinobacteria  Otu0012    0.586797  0.120321       0.119248   
12           Actinobacteria  Otu0013    0.581907  0.032502       0.039782   
13            Rubrobacteria  Otu0014    0.593458  0.105370       0.114286   
14           Actinobacteria  Otu0015    0.610294  0.068264       0.042355   
15           Actinobacteria  Otu0016    0.572127  0.018585       0.015636   
16      Alphaproteobacteria  Otu0017    0.547030  0.019621       0.017369   
17      Gammaproteobacteria  Otu0018    0.533800  0.000000       0.000000   
18      Deltaproteobacteria  Otu0019    0.565421  0.033989       0.056988   
19      Gammaproteobacteria  Otu0020    0.545455  0.000000       0.000000   
20      Alphaproteobacteria  Otu0021    0.576733  0.010739       0.019427   
21      Alphaproteobacteria  Otu0022    0.576733  0.017602       0.023461   
22      Alphaproteobacteria  Otu0023    0.529703  0.000000       0.000082   
23      Alphaproteobacteria  Otu0024    0.586634  0.016229       0.007244   
24      Alphaproteobacteria  Otu0025    0.564356  0.028341       0.027330   
25           Actinobacteria  Otu0026    0.581907  0.037611       0.036616   
26           Actinobacteria  Otu0027    0.584352  0.025984       0.020881   
27              Bacteroidia  Otu0028    0.508274  0.025624       0.043346   
28      Gammaproteobacteria  Otu0029    0.536131  0.001941       0.000000   
29          Thermoleophilia  Otu0030    0.585082  0.116788       0.132333   
...                     ...      ...         ...       ...            ...   
8602        Thermoleophilia  Otu8603    0.592075  0.000000       0.000000   
8603          Elusimicrobia  Otu8604    0.549528  0.000000       0.000000   
8604         Acidimicrobiia  Otu8605    0.595533  0.000000       0.000000   
8605               Subgroup  Otu8606    0.593458  0.001996       0.000000   
8606           Unclassified  Otu8607    0.474453  0.000000       0.000000   
8607           Unclassified  Otu8608    0.519814  0.000000       0.000000   
8608                Bacilli  Otu8609    0.551402  0.000000       0.000000   
8609       Planctomycetacia  Otu8610    0.544335  0.000000       0.000000   
8610    Gammaproteobacteria  Otu8611    0.552448  0.000000       0.000000   
8611         Entotheonellia  Otu8612    0.558313  0.000000       0.000000   
8612    Deltaproteobacteria  Otu8613    0.586047  0.000000       0.000000   
8613    Alphaproteobacteria  Otu8614    0.533499  0.000081       0.000082   
8614    Gammaproteobacteria  Otu8615    0.572093  0.000000       0.000000   
8615             Chlamydiae  Otu8616    0.517483  0.000000       0.000000   
8616           Unclassified  Otu8617    0.542056  0.000000       0.000000   
8617    Deltaproteobacteria  Otu8618    0.561772  0.000000       0.000000   
8618                 BD2-11  Otu8619    0.602326  0.047619       0.020833   
8619    Alphaproteobacteria  Otu8620    0.574257  0.000000       0.000000   
8620    Gammaproteobacteria  Otu8621    0.565421  0.000000       0.000000   
8621       Planctomycetacia  Otu8622    0.654846  0.000000       0.000000

The resulting data frame is "melted" such that the enzymatic conditions become a new column and the GC content and value are the only two numerical value columns.

In [69]:
df4 = df3.melt(id_vars=["Class", "OTU", "GC_content"])

By summarizing within each Class and Enzyme category, we should receive either 1 or 0 if a group is not present in a given category. 

In [70]:
df4.groupby(["Class", "Enzyme"]).sum()

GC_content  value
Class               Enzyme                          
0319-7L14           Promega42       32.813589    1.0
                    Promega55       32.813589    1.0
                    SuperScriptIV   32.813589    1.0
                    TGIRT           32.813589    1.0
ABY1                Promega42        0.523342    0.0
                    Promega55        0.523342    0.0
                    SuperScriptIV    0.523342    0.0
                    TGIRT            0.523342    0.0
AKAU4049            Promega42        1.188372    0.0
                    Promega55        1.188372    1.0
                    SuperScriptIV    1.188372    1.0
                    TGIRT            1.188372    1.0
Acidimicrobiia      Promega42      150.930098    1.0
                    Promega55      150.930098    1.0
                    SuperScriptIV  150.930098    1.0
                    TGIRT          150.930098    1.0
Acidobacteriia      Promega42       17.139303    1.0
                    Promega55       17.139303    1.0
                    SuperScriptIV   17.139303    1.0
                    TGIRT           17.139303    1.0
Actinobacteria      Promega42      355.271244    1.0
                    Promega55      355.271244    1.0
                    SuperScriptIV  355.271244    1.0
                    TGIRT          355.271244    1.0
Alphaproteobacteria Promega42      418.264794    1.0
                    Promega55      418.264794    1.0
                    SuperScriptIV  418.264794    1.0
                    TGIRT          418.264794    1.0
Anaerolineae        Promega42       44.794870    1.0
                    Promega55       44.794870    1.0
...                                       ...    ...
Thermoplasmata      SuperScriptIV    5.766839    1.0
                    TGIRT            5.766839    1.0
Unclassified        Promega42      456.057911    1.0
                    Promega55      456.057911    1.0
                    SuperScriptIV  456.057911    1.0
                    TGIRT          456.057911    1.0
Verrucomicrobiae    Promega42      152.078024    1.0
                    Promega55      152.078024    1.0
                    SuperScriptIV  152.078024    1.0
                    TGIRT          152.078024    1.0
WS6                 Promega42        2.930980    0.0
                    Promega55        2.930980    0.0
                    SuperScriptIV    2.930980    1.0
                    TGIRT            2.930980    1.0
WWE3                Promega42        0.512376    0.0
                    Promega55        0.512376    0.0
                    SuperScriptIV    0.512376    0.0
                    TGIRT            0.512376    0.0
Woesearchaeia       Promega42        0.526992    0.0
                    Promega55        0.526992    1.0
                    SuperScriptIV    0.526992    0.0
                    TGIRT            0.526992    0.0
uncultured          Promega42       60.233086    1.0
                    Promega55       60.233086    1.0
                    SuperScriptIV   60.233086    1.0
                    TGIRT           60.233086    1.0
vadinHA49           Promega42        3.410197    1.0
                    Promega55        3.410197    1.0
                    SuperScriptIV    3.410197    1.0
                    TGIRT            3.410197    1.0

[324 rows x 2 columns]

Multiplying a GC content value of each OTU by the OTU's relative abundance within a given Class and Enzyme group, we receive the OTU's proportional contribution to the overall Class GC content. By summarizing the GC content over a Class, we obtain it's weighted average GC content. The Class normalized count is discarded. 

In [71]:
df4.GC_content = df4.GC_content*df4.value
df5 = df4.groupby(["Class","Enzyme"]).sum()
df5 = df5.drop("value", axis=1)
df5 

GC_content
Class               Enzyme                   
0319-7L14           Promega42        0.580750
                    Promega55        0.582987
                    SuperScriptIV    0.581233
                    TGIRT            0.582942
ABY1                Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
AKAU4049            Promega42        0.000000
                    Promega55        0.593023
                    SuperScriptIV    0.593798
                    TGIRT            0.594186
Acidimicrobiia      Promega42        0.585221
                    Promega55        0.586662
                    SuperScriptIV    0.588191
                    TGIRT            0.587488
Acidobacteriia      Promega42        0.555791
                    Promega55        0.561708
                    SuperScriptIV    0.561813
                    TGIRT            0.559804
Actinobacteria      Promega42        0.583321
                    Promega55        0.583805
                    SuperScriptIV    0.584725
                    TGIRT            0.586320
Alphaproteobacteria Promega42        0.554835
                    Promega55        0.553426
                    SuperScriptIV    0.562606
                    TGIRT            0.563610
Anaerolineae        Promega42        0.552375
                    Promega55        0.559423
...                                       ...
Thermoplasmata      SuperScriptIV    0.580311
                    TGIRT            0.577720
Unclassified        Promega42        0.492766
                    Promega55        0.507756
                    SuperScriptIV    0.505267
                    TGIRT            0.503933
Verrucomicrobiae    Promega42        0.534486
                    Promega55        0.533333
                    SuperScriptIV    0.532315
                    TGIRT            0.532096
WS6                 Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.496296
                    TGIRT            0.496296
WWE3                Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
Woesearchaeia       Promega42        0.000000
                    Promega55        0.526992
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
uncultured          Promega42        0.608757
                    Promega55        0.612651
                    SuperScriptIV    0.611116
                    TGIRT            0.616270
vadinHA49           Promega42        0.568613
                    Promega55        0.569948
                    SuperScriptIV    0.570093
                    TGIRT            0.570093

[324 rows x 1 columns]

In [72]:
df2 = df1.groupby("Class").sum()
df2 = df2.reset_index()
df2 = df2.melt(id_vars="Class")
df2 = df2.set_index(["Class", "Enzyme"])
df2 = df2.sort_values(["Class", "Enzyme"])
df2

value
Class               Enzyme              
0319-7L14           Promega42        527
                    Promega55        442
                    SuperScriptIV    332
                    TGIRT            392
ABY1                Promega42          0
                    Promega55          0
                    SuperScriptIV      0
                    TGIRT              0
AKAU4049            Promega42          0
                    Promega55          1
                    SuperScriptIV      3
                    TGIRT              4
Acidimicrobiia      Promega42       1203
                    Promega55       1617
                    SuperScriptIV   1518
                    TGIRT           1858
Acidobacteriia      Promega42        257
                    Promega55        259
                    SuperScriptIV    444
                    TGIRT            359
Actinobacteria      Promega42       5864
                    Promega55      11263
                    SuperScriptIV  10105
                    TGIRT          11353
Alphaproteobacteria Promega42      12943
                    Promega55       9302
                    SuperScriptIV  12148
                    TGIRT          12385
Anaerolineae        Promega42        191
                    Promega55        175
...                                  ...
Thermoplasmata      SuperScriptIV      5
                    TGIRT              4
Unclassified        Promega42       1211
                    Promega55       1210
                    SuperScriptIV   1292
                    TGIRT           1216
Verrucomicrobiae    Promega42       1310
                    Promega55        620
                    SuperScriptIV   1391
                    TGIRT           1029
WS6                 Promega42          0
                    Promega55          0
                    SuperScriptIV      2
                    TGIRT              1
WWE3                Promega42          0
                    Promega55          0
                    SuperScriptIV      0
                    TGIRT              0
Woesearchaeia       Promega42          0
                    Promega55          2
                    SuperScriptIV      0
                    TGIRT              0
uncultured          Promega42         41
                    Promega55         66
                    SuperScriptIV     31
                    TGIRT             28
vadinHA49           Promega42          7
                    Promega55          7
                    SuperScriptIV      1
                    TGIRT              1

[324 rows x 1 columns]

In [108]:
dfFinal = pd.concat([df2, df5],axis=1)
dfFinal

value  GC_content
Class               Enzyme                          
0319-7L14           Promega42        527    0.580750
                    Promega55        442    0.582987
                    SuperScriptIV    332    0.581233
                    TGIRT            392    0.582942
ABY1                Promega42          0    0.000000
                    Promega55          0    0.000000
                    SuperScriptIV      0    0.000000
                    TGIRT              0    0.000000
AKAU4049            Promega42          0    0.000000
                    Promega55          1    0.593023
                    SuperScriptIV      3    0.593798
                    TGIRT              4    0.594186
Acidimicrobiia      Promega42       1203    0.585221
                    Promega55       1617    0.586662
                    SuperScriptIV   1518    0.588191
                    TGIRT           1858    0.587488
Acidobacteriia      Promega42        257    0.555791
                    Promega55        259    0.561708
                    SuperScriptIV    444    0.561813
                    TGIRT            359    0.559804
Actinobacteria      Promega42       5864    0.583321
                    Promega55      11263    0.583805
                    SuperScriptIV  10105    0.584725
                    TGIRT          11353    0.586320
Alphaproteobacteria Promega42      12943    0.554835
                    Promega55       9302    0.553426
                    SuperScriptIV  12148    0.562606
                    TGIRT          12385    0.563610
Anaerolineae        Promega42        191    0.552375
                    Promega55        175    0.559423
...                                  ...         ...
Thermoplasmata      SuperScriptIV      5    0.580311
                    TGIRT              4    0.577720
Unclassified        Promega42       1211    0.492766
                    Promega55       1210    0.507756
                    SuperScriptIV   1292    0.505267
                    TGIRT           1216    0.503933
Verrucomicrobiae    Promega42       1310    0.534486
                    Promega55        620    0.533333
                    SuperScriptIV   1391    0.532315
                    TGIRT           1029    0.532096
WS6                 Promega42          0    0.000000
                    Promega55          0    0.000000
                    SuperScriptIV      2    0.496296
                    TGIRT              1    0.496296
WWE3                Promega42          0    0.000000
                    Promega55          0    0.000000
                    SuperScriptIV      0    0.000000
                    TGIRT              0    0.000000
Woesearchaeia       Promega42          0    0.000000
                    Promega55          2    0.526992
                    SuperScriptIV      0    0.000000
                    TGIRT              0    0.000000
uncultured          Promega42         41    0.608757
                    Promega55         66    0.612651
                    SuperScriptIV     31    0.611116
                    TGIRT             28    0.616270
vadinHA49           Promega42          7    0.568613
                    Promega55          7    0.569948
                    SuperScriptIV      1    0.570093
                    TGIRT              1    0.570093

[324 rows x 2 columns]

In [109]:
dfFinal = dfFinal.reset_index()
dfFinal = dfFinal.pivot(index="Class", columns="Enzyme")
dfFinal

value                                GC_content  \
Enzyme                 Promega42 Promega55 SuperScriptIV  TGIRT  Promega42   
Class                                                                        
0319-7L14                    527       442           332    392   0.580750   
ABY1                           0         0             0      0   0.000000   
AKAU4049                       0         1             3      4   0.000000   
Acidimicrobiia              1203      1617          1518   1858   0.585221   
Acidobacteriia               257       259           444    359   0.555791   
Actinobacteria              5864     11263         10105  11353   0.583321   
Alphaproteobacteria        12943      9302         12148  12385   0.554835   
Anaerolineae                 191       175           113     89   0.552375   
Armatimonadia                  6        19             1      2   0.579068   
BD2-11                        26        33            48     42   0.609861   
BD7-11                         7         4             4      0   0.579222   
Babeliae                      11        10            18      9   0.581275   
Bacilli                     1356       656           663    520   0.522874   
Bacteroidia                 2825      1817          2307   3005   0.514352   
Berkelbacteria                 2         0             1      0   0.509901   
Blastocatellia               336       243           309    328   0.543584   
Chlamydiae                    25        23             6      3   0.502278   
Chloroflexia                 441       825           666    789   0.639146   
Chthonomonadetes               0         0             0      0   0.000000   
Clostridia                    13        13             8     16   0.530663   
Coriobacteriia                 1         0             0      0   0.580882   
Dehalococcoidia               70        98           155     97   0.578148   
Deinococci                    89        28            44     29   0.565357   
Deltaproteobacteria         4330      2154          3141   3001   0.563930   
Elusimicrobia                  6         0             2      2   0.547658   
Entotheonellia               125       122           221    164   0.576794   
Erysipelotrichia               0         1             5      0   0.000000   
FFCH5909                       0         0             1      0   0.000000   
Fibrobacteria                 45        35            46     36   0.554449   
Fimbriimonadia                69        29            32     43   0.542453   
...                          ...       ...           ...    ...        ...   
Nitrospira                    32        34            74     70   0.600736   
OLB14                         23        24            44     56   0.586957   
OM190                          0         0             0      0   0.000000   
Oxyphotobacteria            2798       962          1711    877   0.546075   
P2-11E                         7         3             3      3   0.575309   
Parcubacteria                  3         1             0      2   0.500000   
Phycisphaerae                101       128            18     17   0.576535   
Pla4                           8         4             3      8   0.603730   
Planctomycetacia             357       710           247    283   0.598206   
Rhodothermia                   0        11            10      5   0.000000   
Rubrobacteria               1351      1505          2380   1974   0.597608   
S0134                        116        75            73    114   0.589186   
SHA-26                         4        12            16      4   0.602650   
Saccharimonadia              130        57            49     30   0.503040   
Sericytochromatia             53        25            33     27   0.532618   
Spirochaetia                   0         1             0      0   0.000000   
Subgroup                     385       284           681    501   0.580126   
Synergistia                    0         0       

In [91]:
dfFinal.to_csv("GC_class_whole.csv")

Only bacterial classes that account for the upper quartile of the dataset will be plotted. The remaining groups are summarized and labeled as "Low abundance".

In [112]:
# Using row sums to normalize each class
rowSums = dfFinal.sum(axis=1, level=0)["value"]

# 85 % quantile
quantile85 = rowSums.quantile(q=0.5)
rowSumsVector = rowSums <= quantile85

# Upper 85% quantile rows
df3 = dfFinal.loc[rowSums >= quantile85, :]
la = dfFinal.loc[rowSums < quantile85, :].sum(axis=0)

In [113]:
# Pulling lower quantile rows together and appending them to the upper quantile data frame
la = la.to_frame(name="Low abundance")
la = la.transpose()

df3 = df3.append(la)
df3

value                                  GC_content  \
Enzyme              Promega42 Promega55 SuperScriptIV    TGIRT  Promega42   
0319-7L14               527.0     442.0         332.0    392.0   0.580750   
Acidimicrobiia         1203.0    1617.0        1518.0   1858.0   0.585221   
Acidobacteriia          257.0     259.0         444.0    359.0   0.555791   
Actinobacteria         5864.0   11263.0       10105.0  11353.0   0.583321   
Alphaproteobacteria   12943.0    9302.0       12148.0  12385.0   0.554835   
Anaerolineae            191.0     175.0         113.0     89.0   0.552375   
BD2-11                   26.0      33.0          48.0     42.0   0.609861   
Bacilli                1356.0     656.0         663.0    520.0   0.522874   
Bacteroidia            2825.0    1817.0        2307.0   3005.0   0.514352   
Blastocatellia          336.0     243.0         309.0    328.0   0.543584   
Chloroflexia            441.0     825.0         666.0    789.0   0.639146   
Dehalococcoidia          70.0      98.0         155.0     97.0   0.578148   
Deinococci               89.0      28.0          44.0     29.0   0.565357   
Deltaproteobacteria    4330.0    2154.0        3141.0   3001.0   0.563930   
Entotheonellia          125.0     122.0         221.0    164.0   0.576794   
Fibrobacteria            45.0      35.0          46.0     36.0   0.554449   
Fimbriimonadia           69.0      29.0          32.0     43.0   0.542453   
Gammaproteobacteria    5967.0    7610.0        2793.0   2576.0   0.543056   
Gemmatimonadetes        532.0     591.0         518.0    463.0   0.626024   
Gitt-GS-136             270.0     171.0         239.0    274.0   0.560948   
Holophagae              235.0     139.0         308.0    191.0   0.567214   
JG30-KF-CM66             76.0     145.0         175.0    175.0   0.596772   
KD4-96                  298.0     264.0         370.0    406.0   0.569651   
Ktedonobacteria          26.0      41.0          61.0     52.0   0.578646   
Longimicrobia           328.0     217.0         213.0    197.0   0.615191   
MB-A2-108                61.0     101.0          67.0     99.0   0.608917   
Nitriliruptoria         253.0     380.0         410.0    408.0   0.576569   
Nitrospira               32.0      34.0          74.0     70.0   0.600736   
Oxyphotobacteria       2798.0     962.0        1711.0    877.0   0.546075   
Phycisphaerae           101.0     128.0          18.0     17.0   0.576535   
Planctomycetacia        357.0     710.0         247.0    283.0   0.598206   
Rubrobacteria          1351.0    1505.0        2380.0   1974.0   0.597608   
S0134                   116.0      75.0          73.0    114.0   0.589186   
Saccharimonadia         130.0      57.0          49.0     30.0   0.503040   
Subgroup                385.0     284.0         681.0    501.0   0.580126   
TK10                    275.0     583.0         522.0    611.0   0.614815   
Thermoanaerobaculia     117.0     127.0         122.0    146.0   0.582242   
Thermoleophilia        2745.0    4643.0        3733.0   3562.0   0.589096   
Unclassified           1211.0    1210.0        1292.0   1216.0   0.492766   
Verrucomicrobiae       1310.0     620.0        1391.0   1029.0   0.534486   
uncultured               41.0      66.0          31.0     28.0   0.608757   
Low abundance           288.0     239.0         230.0    211.0  13.216608   

                                                         
Enzyme               Promega55 SuperScriptIV      TGIRT  
0319-7L14             0.582987      0.581233   0.582942  
Acidimicrobiia        0.586662      0.588191   0.587488  
Acidobacteriia        0.561708      0.561813   0.559804  
Actinobacteria        0.583805      0.584725   0.586320  
Alphaproteobacteria   0.553426      0.562606   0.563610  
Anaerolineae          0.559423      0.561238   0.564171  
BD2-11                0.610253      0.608890   0.610935  
Bacilli               0.533793      0.531269   0.537584  
Bacteroidia           0.514383      0.513738   0.508924

In [114]:
df3.to_csv("GC_class_forFigure.csv")

In [129]:
df3.sum(axis=1)

Oxyphotobacteria       0.12170
Actinobacteria         0.76432
Alphaproteobacteria    0.95186
Gammaproteobacteria    0.37750
Deltaproteobacteria    0.24800
Rubrobacteria          0.15054
Bacteroidia            0.19058
Thermoleophilia        0.29908
Verrucomicrobiae       0.08730
KD4-96                 0.02764
Nitriliruptoria        0.02952
Acidimicrobiia         0.12432
Bacilli                0.06234
Acidobacteriia         0.02648
Unclassified           0.09806
TK10                   0.03926
Gemmatimonadetes       0.04232
0319-7L14              0.03426
Chloroflexia           0.05230
Subgroup               0.03688
Planctomycetacia       0.03190
Low abundance          0.20384
dtype: float64

In [31]:
df3.to_csv("barplot_data_class.csv")

In [33]:
df3 = df3.reset_index().melt(id_vars="index")

df3.columns = ["Phylum", "Enzyme", "Value"]

df3

Phylum         Enzyme    Value
0      Oxyphotobacteria          TGIRT  0.01930
1        Actinobacteria          TGIRT  0.21342
2   Alphaproteobacteria          TGIRT  0.26292
3   Gammaproteobacteria          TGIRT  0.04878
4   Deltaproteobacteria          TGIRT  0.06152
5         Rubrobacteria          TGIRT  0.04210
6           Bacteroidia          TGIRT  0.05900
7       Thermoleophilia          TGIRT  0.07198
8      Verrucomicrobiae          TGIRT  0.02250
9                KD4-96          TGIRT  0.00862
10      Nitriliruptoria          TGIRT  0.00826
11       Acidimicrobiia          TGIRT  0.03412
12              Bacilli          TGIRT  0.01122
13       Acidobacteriia          TGIRT  0.00734
14         Unclassified          TGIRT  0.02382
15                 TK10          TGIRT  0.01146
16     Gemmatimonadetes          TGIRT  0.00952
17            0319-7L14          TGIRT  0.00800
18         Chloroflexia          TGIRT  0.01416
19             Subgroup          TGIRT  0.00960
20     Planctomycetacia          TGIRT  0.00472
21        Low abundance          TGIRT  0.04764
22     Oxyphotobacteria  SuperScriptIV  0.03422
23       Actinobacteria  SuperScriptIV  0.20210
24  Alphaproteobacteria  SuperScriptIV  0.24296
25  Gammaproteobacteria  SuperScriptIV  0.05586
26  Deltaproteobacteria  SuperScriptIV  0.06282
27        Rubrobacteria  SuperScriptIV  0.04760
28          Bacteroidia  SuperScriptIV  0.04614
29      Thermoleophilia  SuperScriptIV  0.07466
..                  ...            ...      ...
58         Unclassified      Promega42  0.02422
59                 TK10      Promega42  0.00550
60     Gemmatimonadetes      Promega42  0.01064
61            0319-7L14      Promega42  0.01054
62         Chloroflexia      Promega42  0.00882
63             Subgroup      Promega42  0.00770
64     Planctomycetacia      Promega42  0.00714
65        Low abundance      Promega42  0.05544
66     Oxyphotobacteria      Promega55  0.01222
67       Actinobacteria      Promega55  0.23152
68  Alphaproteobacteria      Promega55  0.18712
69  Gammaproteobacteria      Promega55  0.15352
70  Deltaproteobacteria      Promega55  0.03706
71        Rubrobacteria      Promega55  0.03382
72          Bacteroidia      Promega55  0.02894
73      Thermoleophilia      Promega55  0.09754
74     Verrucomicrobiae      Promega55  0.01078
75               KD4-96      Promega55  0.00566
76      Nitriliruptoria      Promega55  0.00800
77       Acidimicrobiia      Promega55  0.03578
78              Bacilli      Promega55  0.01074
79       Acidobacteriia      Promega55  0.00512
80         Unclassified      Promega55  0.02418
81                 TK10      Promega55  0.01186
82     Gemmatimonadetes      Promega55  0.01180
83            0319-7L14      Promega55  0.00908
84         Chloroflexia      Promega55  0.01600
85             Subgroup      Promega55  0.00596
86     Planctomycetacia      Promega55  0.01510
87        Low abundance      Promega55  0.04820

[88 rows x 3 columns]

In [34]:
# Simplifying a multi index into just one index 
idx = pd.IndexSlice

df1 = data.data.copy()

df1 = df1.sum(level="Enzyme", axis=1)

df1 = df1.reset_index()

df1 = df1.iloc[:,1:]

df1 = df1.iloc[:,[1,5,6,7,8,9,10]]

In [35]:
df1.index = df1.OTU

df1 = df1.drop("OTU", axis=1)

In [36]:
colNames = list(df1.columns.get_level_values("Enzyme"))
colNames[1] = "GC"
colNames

df1.columns = colNames

del df1.index.name

In [104]:
df1melted = df1.melt(id_vars=["Class", "GC"])
df1melted

Class        GC   variable  value
0         Oxyphotobacteria  0.547847      TGIRT    825
1           Actinobacteria  0.572127      TGIRT   1834
2      Alphaproteobacteria  0.579208      TGIRT   1798
3      Gammaproteobacteria  0.550117      TGIRT    107
4      Alphaproteobacteria  0.559406      TGIRT   1835
5      Alphaproteobacteria  0.522277      TGIRT    678
6      Alphaproteobacteria  0.564356      TGIRT    458
7      Alphaproteobacteria  0.559406      TGIRT    639
8      Alphaproteobacteria  0.574257      TGIRT    364
9      Deltaproteobacteria  0.567757      TGIRT    644
10           Rubrobacteria  0.602804      TGIRT    627
11          Actinobacteria  0.586797      TGIRT   1194
12          Actinobacteria  0.581907      TGIRT    396
13           Rubrobacteria  0.593458      TGIRT    233
14          Actinobacteria  0.610294      TGIRT    658
15          Actinobacteria  0.572127      TGIRT    197
16     Alphaproteobacteria  0.547030      TGIRT    258
17     Gammaproteobacteria  0.533800      TGIRT      0
18     Deltaproteobacteria  0.565421      TGIRT     92
19     Gammaproteobacteria  0.545455      TGIRT      0
20     Alphaproteobacteria  0.576733      TGIRT    165
21     Alphaproteobacteria  0.576733      TGIRT    231
22     Alphaproteobacteria  0.529703      TGIRT      0
23     Alphaproteobacteria  0.586634      TGIRT    167
24     Alphaproteobacteria  0.564356      TGIRT    351
25          Actinobacteria  0.581907      TGIRT    407
26          Actinobacteria  0.584352      TGIRT    267
27             Bacteroidia  0.508274      TGIRT    106
28     Gammaproteobacteria  0.536131      TGIRT      5
29         Thermoleophilia  0.585082      TGIRT    410
...                    ...       ...        ...    ...
34498      Thermoleophilia  0.592075  Promega55      0
34499        Elusimicrobia  0.549528  Promega55      0
34500       Acidimicrobiia  0.595533  Promega55      0
34501             Subgroup  0.593458  Promega55      0
34502         Unclassified  0.474453  Promega55      0
34503         Unclassified  0.519814  Promega55      0
34504              Bacilli  0.551402  Promega55      0
34505     Planctomycetacia  0.544335  Promega55      0
34506  Gammaproteobacteria  0.552448  Promega55      0
34507       Entotheonellia  0.558313  Promega55      0
34508  Deltaproteobacteria  0.586047  Promega55      0
34509  Alphaproteobacteria  0.533499  Promega55      0
34510  Gammaproteobacteria  0.572093  Promega55      0
34511           Chlamydiae  0.517483  Promega55      0
34512         Unclassified  0.542056  Promega55      0
34513  Deltaproteobacteria  0.561772  Promega55      0
34514               BD2-11  0.602326  Promega55      0
34515  Alphaproteobacteria  0.574257  Promega55      0
34516  Gammaproteobacteria  0.565421  Promega55      1
34517     Planctomycetacia  0.654846  Promega55      0
34518  Gammaproteobacteria  0.561772  Promega55      1
34519         Unclassified  0.589109  Promega55      0
34520  Gammaproteobacteria  0.568765  Promega55      0
34521       Acidimicrobiia  0.570370  Promega55      0
34522           Holophagae  0.580420  Promega55      0
34523       Microgenomatia  0.494975  Promega55      0
34524     Planctomycetacia  0.665871  Promega55      0
34525  Deltaproteobacteria  0.570025  Promega55      0
34526      Saccharimonadia  0.506173  Promega55      0
34527       Actinobacteria  0.582927  Promega55      0

[34528 rows x 4 columns]

In [105]:
colSum = df1melted.groupby("variable").sum()["value"]

colSum["Promega42"]

newValue = []
# Dividing each row value by an appropriate total sum of the category (enzyme)
for row in df1melted.iterrows():
    newValue.append(row[1].value/colSum[row[1].variable])
    
df1melted["value"] = newValue

In [111]:
df1sum = df1melted.groupby(["Class", "variable"]).sum()

In [121]:
df1melted.groupby(["Class", "variable"]).mean()

GC     value
Class               variable                         
0319-7L14           Promega42      0.585957  0.000188
                    Promega55      0.585957  0.000162
                    SuperScriptIV  0.585957  0.000119
                    TGIRT          0.585957  0.000143
ABY1                Promega42      0.523342  0.000000
                    Promega55      0.523342  0.000000
                    SuperScriptIV  0.523342  0.000000
                    TGIRT          0.523342  0.000000
AKAU4049            Promega42      0.594186  0.000000
                    Promega55      0.594186  0.000010
                    SuperScriptIV  0.594186  0.000030
                    TGIRT          0.594186  0.000040
Acidimicrobiia      Promega42      0.585000  0.000093
                    Promega55      0.585000  0.000139
                    SuperScriptIV  0.585000  0.000118
                    TGIRT          0.585000  0.000132
Acidobacteriia      Promega42      0.571310  0.000171
                    Promega55      0.571310  0.000171
                    SuperScriptIV  0.571310  0.000296
                    TGIRT          0.571310  0.000245
Actinobacteria      Promega42      0.584328  0.000193
                    Promega55      0.584328  0.000381
                    SuperScriptIV  0.584328  0.000332
                    TGIRT          0.584328  0.000351
Alphaproteobacteria Promega42      0.563699  0.000349
                    Promega55      0.563699  0.000252
                    SuperScriptIV  0.563699  0.000327
                    TGIRT          0.563699  0.000354
Anaerolineae        Promega42      0.567024  0.000048
                    Promega55      0.567024  0.000042
...                                     ...       ...
Thermoplasmata      SuperScriptIV  0.576684  0.000010
                    TGIRT          0.576684  0.000006
Unclassified        Promega42      0.537804  0.000029
                    Promega55      0.537804  0.000029
                    SuperScriptIV  0.537804  0.000030
                    TGIRT          0.537804  0.000028
Verrucomicrobiae    Promega42      0.535486  0.000092
                    Promega55      0.535486  0.000038
                    SuperScriptIV  0.535486  0.000098
                    TGIRT          0.535486  0.000079
WS6                 Promega42      0.488497  0.000000
                    Promega55      0.488497  0.000000
                    SuperScriptIV  0.488497  0.000007
                    TGIRT          0.488497  0.000003
WWE3                Promega42      0.512376  0.000000
                    Promega55      0.512376  0.000000
                    SuperScriptIV  0.512376  0.000000
                    TGIRT          0.512376  0.000000
Woesearchaeia       Promega42      0.526992  0.000000
                    Promega55      0.526992  0.000040
                    SuperScriptIV  0.526992  0.000000
                    TGIRT          0.526992  0.000000
uncultured          Promega42      0.608415  0.000008
                    Promega55      0.608415  0.000012
                    SuperScriptIV  0.608415  0.000006
                    TGIRT          0.608415  0.000005
vadinHA49           Promega42      0.568366  0.000023
                    Promega55      0.568366  0.000023
                    SuperScriptIV  0.568366  0.000003
                    TGIRT          0.568366  0.000003

[324 rows x 2 columns]

In [116]:
for row in df1melted.iterrows():
    # For a future convenience
    row=row[1]
    classval = row.Class
    enzyme = row.variable
    print(classval, enzyme)
    break

Oxyphotobacteria TGIRT


In [118]:
idx = pd.IndexSlice
df1sum.loc[idx[classval, enzyme],idx["value"]]

0.019299999999999994

In [120]:
df1sum.loc[idx[classval, enzyme],:]

GC       37.620606
value     0.019300
Name: (Oxyphotobacteria, TGIRT), dtype: float64

In [62]:
df1.to_csv("data_for_gc_plot.csv")

|Enzyme        |TGIRT  |SuperScriptIV|Promega42  |Promega55|
|:-------------|:-----:|:-----------:|:---------:|:-------:|
|TGIRT         | x     | TvS         | Tv42      | Tv55    |  
|SuperScriptIV | TvS   | x           | Sv42      | Sv55    |
|Promega42     | Tv42  | Sv42        | x         | P42v55  |
|Promega55     | Tv55  | Sv55        | P42v55    | x       |